# Setup

In [1]:
import os
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
from random import randint
import math
from datetime import datetime
import pickle

from sklearn.svm import SVC
from sklearn import metrics
from sklearn.metrics import roc_curve
from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import classification_report
from sklearn.metrics import precision_recall_curve
from sklearn.metrics import roc_curve
from sklearn.metrics import balanced_accuracy_score
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.metrics import roc_auc_score

In [2]:
os.getcwd()

'D:\\Github\\Stomach-Status-Classification\\Experiment\\Approach2-8\\SVM'

In [3]:
for i in range(3):
    os.chdir("..")

In [4]:
os.getcwd()

'D:\\Github\\Stomach-Status-Classification'

In [5]:
main_data_dir = os.getcwd() + "\\Data set"
kmean_data_dir = main_data_dir + "\\kmean_dataset2-8"
kmean_data_10cv_dir = kmean_data_dir + "\\10cv_512"
import glob

kmean_data_10cv_lst = [x for x in glob.glob(kmean_data_10cv_dir + '\\*') if 'surf' in x and 'index' in x and '50' in x]
print(kmean_data_10cv_lst)

['D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_test_50_4_3_True_Falsehisto_512_cv_index0.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_test_50_4_3_True_Falsehisto_512_cv_index1.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_test_50_4_3_True_Falsehisto_512_cv_index2.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_test_50_4_3_True_Falsehisto_512_cv_index3.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_test_50_4_3_True_Falsehisto_512_cv_index4.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_test_50_4_3_True_Falsehisto_512_cv_index5.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_test_50_4_3_True_Falsehisto_512_cv_index6.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\

In [6]:
kmean_train_paths = [x for x in kmean_data_10cv_lst if 'train' in x]
kmean_test_paths = [x for x in kmean_data_10cv_lst if 'test' in x]
print(kmean_train_paths)
print()
print(kmean_test_paths)
print(len(kmean_train_paths))
print(len(kmean_test_paths))

['D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_train_50_4_3_True_Falsehisto_512_cv_index0.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_train_50_4_3_True_Falsehisto_512_cv_index1.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_train_50_4_3_True_Falsehisto_512_cv_index2.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_train_50_4_3_True_Falsehisto_512_cv_index3.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_train_50_4_3_True_Falsehisto_512_cv_index4.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_train_50_4_3_True_Falsehisto_512_cv_index5.csv', 'D:\\Github\\Stomach-Status-Classification\\Data set\\kmean_dataset2-8\\10cv_512\\surf_train_50_4_3_True_Falsehisto_512_cv_index6.csv', 'D:\\Github\\Stomach-Status-Classification\\Dat

In [7]:
def to_categorical(y, num_classes=None, dtype='float32'):
    """to_categorical _summary_

    Arguments:
        y -- The label of the data set with the shape of [None, 1]

    Keyword Arguments:
        num_classes -- The num_classes in the data set (default: {None})
        dtype -- the type of each element of the label after reshape (default: {'float32'})

    Returns:
        the label of the data set with the shape of [number of samples, number of classes].
    """    
    y = np.array(y, dtype='int')
    input_shape = y.shape
    if input_shape and input_shape[-1] == 1 and len(input_shape) > 1:
        input_shape = tuple(input_shape[:-1])
    y = y.ravel()
    if not num_classes:
        num_classes = np.max(y) + 1
    n = y.shape[0]
    categorical = np.zeros((n, num_classes), dtype=dtype)
    categorical[np.arange(n), y] = 1
    output_shape = input_shape + (num_classes,)
    categorical = np.reshape(categorical, output_shape)
    return categorical

In [8]:
class roc_curve_score:
    def __init__(self, y_true, y_pred, num_class):
        self.y_test = to_categorical(y_true)
        self.y_score = to_categorical(y_pred)
        print(np.unique(self.y_test), np.unique(self.y_score))
        self.fprs = {}
        self.tprs = {}
        self.thresh_holds = {}
        for x in range(num_class):
            self.fprs[x], self.tprs[x], self.thresh_holds[x] = roc_curve(self.y_test[:, x], self.y_score[:, x], drop_intermediate=False)
            self.fprs[x] = self.fprs[x].tolist()
            self.tprs[x] = self.tprs[x].tolist()
            self.thresh_holds[x] = self.thresh_holds[x].tolist()
        
        self.fpr_micro_avg, self.tpr_micro_avg, self.threshold_micro_avg, = roc_curve(self.y_test.ravel(), self.y_score.ravel())
        
        all_fpr = np.unique(np.concatenate([self.fprs[i] for i in range(num_class)]))
        mean_tpr = np.zeros_like(all_fpr)
        for i in range(num_class):
            mean_tpr += np.interp(all_fpr, self.fprs[i], self.tprs[i])
        mean_tpr /= num_class
        self.fpr_macro_avg = all_fpr.tolist()
        self.tpr_macro_avg = mean_tpr.tolist()
    
    def get_tpr(self, _class = None):
        if(_class):
            return self.tprs[_class]
        else:
            return self.tprs
    
    def get_fpr(self, _class = None):
        if(_class):
            return self.fprs[_class]
        else:
            return self.fprs

    def get_thresholds(self, _class = None):
        if(_class):
            return self.thresh_holds[_class]
        else:
            return self.thresh_holds

    def get_roc_dict(self):
        return {
            "tpr" : self.get_tpr(),
            "fpr" : self.get_fpr(),
            "thresholds" : self.get_thresholds(),
            "fpr_micro_avg" : self.fpr_micro_avg.tolist(),
            "tpr_micro_avg" : self.tpr_micro_avg.tolist(),
            "fpr_macro_avg" : self.fpr_macro_avg,
            "tpr_macro_avg" : self.tpr_macro_avg,
        }

In [9]:
class utils:
    def __init__(self, confusion_matrix, y_true, y_pred):
        """
            - confusion_matrix: 2x2 numpy array
            - y_true: array of label
            - y_pred: array of output value calculated by model
            - fold_count: number of folds
        """
        
        # Initilize all indicator
        self.TP = confusion_matrix[0][0] # true positive
        self.FN = confusion_matrix[1][0] # false negative
        self.FP = confusion_matrix[1][0] # false positive
        self.TN = confusion_matrix[1][1] # true negative
        self.precision = self.TP/(self.FN +  self.TP) # Precision Score - Positive Predictive Value
        self.recall = self.TP / (self.TP + self.FN)
        self.f1_score =  (2 * self.TP) / (2 * self.TP + self.FP + self.FN)
        self.sensitivity = self.TP / (self.TP + self.FN) # True Positive Rate
        self.specificity = self.TN / (self.TN + self.FP) # False Positive Rate
        self.negative_predictive_value = self.TN / (self.TN + self.FN) # Negative Predictive Value
        self.false_negative_rate = self.FN / (self.FN + self.TP) # False Negative Rate
        self.false_positive_rate = self.FP / (self.FP + self.TN) # False Positive Rate
        self.false_discovery_rate = self.FP / (self.FP + self.TP) # False Discovery Rate
        self.false_omission_rate = self.FN / (self.FN + self.TN) # False Ommision Rate
        self.positive_likelihood_ratio = self.sensitivity / self.false_positive_rate # Positive Likelihood Ratio
        self.negative_likelihood_ratio = self.false_negative_rate / self.specificity # Negative Likelihood Ratio
        self.prevalence_threshold = math.sqrt(self.false_positive_rate) / (math.sqrt(self.sensitivity) + 
                                                                      math.sqrt(self.false_positive_rate)) # Prevalance Threshold
        self.threat_score = self.TP / (self.TN + self.FN + self.FP) # Threat Score
        self.prevalence = (self.TP + self.FN)/(self.TP + self.FN + self.TN + self.FP) # Prevalance 
        #  Matthews correlation coefficient
        self.matthews_correlation_coefficient = (self.TP*self.TN - self.FN*self.FP) / ((self.TP + self.FP)
                                                                                       *(self.TP + self.FN)
                                                                                       *(self.TN + self.FP)
                                                                                       *(self.TN + self.FN))
        self.fowlkes_mallows_index = math.sqrt(self.sensitivity + self.precision) # Fowlkes–Mallows index
        self.informedness = self.sensitivity + self.specificity - 1 # informedness
        self.markedness = self.precision + self.negative_predictive_value - 1 # markedness
        self.diagnostic_odds_ratio = self.positive_likelihood_ratio / self.negative_likelihood_ratio # Diagnostic odds ratio
        self.accuracy = (self.TP + self.TN) / (self.TP + self.TN + self.FP + self.FN)
        self.balanced_accuracy = (self.sensitivity + self.specificity) / 2
        self.roc_auc_macro = roc_auc_score(y_true, y_pred)
        self.roc_auc_micro = roc_auc_score(y_true, y_pred, average = 'micro')
        self.roc_auc_weighted = roc_auc_score(y_true, y_pred, average = 'weighted')
        self.cls_report = classification_report(y_true, y_pred)
        
        # Initilize the structure of output_dicts
        self.confusion_matrix = {
            "TP" : self.TP,
            "TN" : self.TN,
            "FN" : self.FN,
            "FP" : self.FP,
            "precision" : self.precision,
            "recall" : self.recall,
            "f1_score" : self.f1_score,
            "sensitivity" : self.sensitivity,
            "specificity" : self.specificity,
            "negative_predictive_value" : self.negative_predictive_value,
            "false_negative_rate" : self.false_negative_rate,
            "false_positive_rate" : self.false_positive_rate,
            "false_discovery_rate" : self.false_discovery_rate,
            "false_omission_rate" : self.false_omission_rate,
            "Positive_likelihood_ratio" : self.positive_likelihood_ratio,
            "Negative_likelihood_ratio" : self.negative_likelihood_ratio,
            "prevalence_threshold" : self.prevalence_threshold,
            "threat_score" : self.threat_score,
            "Prevalence" : self.prevalence,
            "Matthews_correlation_coefficient" : self.matthews_correlation_coefficient,
            "Fowlkes_Mallows_index" : self.fowlkes_mallows_index,
            "informedness" : self.informedness,
            "markedness" : self.markedness,
            "Diagnostic_odds_ratio" : self.diagnostic_odds_ratio,
            "accuracy" : self.accuracy,
            "balanced_accuracy" : self.balanced_accuracy
        }
        
        self.roc_auc_score = {
            "Macro": self.roc_auc_macro, 
            "Micro": self.roc_auc_micro,
            "Weight": self.roc_auc_weighted
        }
        
#         self.roc_curve = roc_curve_score(y_true=y_true, y_pred=y_pred, num_class=2).get_roc_dict()
        
        self.sub_dict = {
            "Confusion Matrix" : self.confusion_matrix,
            "ROC_AUC_SCORE" : self.roc_auc_score,
            "Classification Report" : classification_report(y_true.tolist(), y_pred.tolist(), 
                                                            labels = [0, 1], # 0 : Licit, 1 : Illicit
                                                            output_dict = True),
#             "ROC_DRAW" : self.roc_curve
        }
    def get_value(self):
        return self.sub_dict
        
# Test 
y_true = np.array([randint(0,1) for x in range(200)])
y_pred = np.array([randint(0,1) for x in range(200)])
confusion_matrix_test = confusion_matrix(y_true, y_pred)
base_utils = utils(confusion_matrix_test, y_true, y_pred)
base_utils.get_value()

{'Confusion Matrix': {'TP': 48,
  'TN': 54,
  'FN': 44,
  'FP': 44,
  'precision': 0.5217391304347826,
  'recall': 0.5217391304347826,
  'f1_score': 0.5217391304347826,
  'sensitivity': 0.5217391304347826,
  'specificity': 0.5510204081632653,
  'negative_predictive_value': 0.5510204081632653,
  'false_negative_rate': 0.4782608695652174,
  'false_positive_rate': 0.4489795918367347,
  'false_discovery_rate': 0.4782608695652174,
  'false_omission_rate': 0.4489795918367347,
  'Positive_likelihood_ratio': 1.1620553359683794,
  'Negative_likelihood_ratio': 0.8679549114331724,
  'prevalence_threshold': 0.481235032753517,
  'threat_score': 0.3380281690140845,
  'Prevalence': 0.4842105263157895,
  'Matthews_correlation_coefficient': 8.070046428354915e-06,
  'Fowlkes_Mallows_index': 1.0215078369104984,
  'informedness': 0.07275953859804796,
  'markedness': 0.07275953859804796,
  'Diagnostic_odds_ratio': 1.3388429752066113,
  'accuracy': 0.5368421052631579,
  'balanced_accuracy': 0.53637976929902

In [10]:
class Training:
    def __init__(self, fold_count, X, y):
        self.fold_count = fold_count
        self.param_grid = {
            "kernel" : ["linear", "rbf", "sigmoid"],
            "degree" : [1, 2, 3, 5, 7, 9],
            "gamma" : ["scale", "auto"],
            "class_weight" : ["balanced", None]
        }
        self.kf = KFold(n_splits=fold_count)
        self.history = {}
        self.X = X
        self.y = y
    
    def get_fold_value(self):
        return self.kf        
        
    def training(self, kernel, degree, gamma, class_weight, train_case):
    
        # output_dict initilize
        output_dict = {}
    
        # poiter track the index of fold
        fold_index = 0
    
        for train_index, test_index in zip(self.X, self.y):
            train_df = pd.read_csv(train_index)
            test_df = pd.read_csv(test_index)
            
            print("\tFold: {}".format(fold_index))
            print("\tTRAIN:", train_index, "\n\tTEST:", test_index)
        
            # folding data
            x_train, y_train = train_df.iloc[:, 2:-1], train_df.iloc[:, -1]
            x_test, y_test = test_df.iloc[:, 2:-1], test_df.iloc[:, -1]
    
            # Training
            print("\t\tTraining : {}".format(fold_index), end = " -- ")
            print("Start: {}".format(datetime.now().strftime("%m/%d/%Y, %H:%M:%S")), end=" --- ")
            model_svc = SVC(kernel = kernel, 
                            degree = degree, 
                            gamma = gamma, 
                            class_weight = class_weight
                           )
            model_svc.fit(x_train,y_train)
            print("End: {}".format(datetime.now().strftime("%m/%d/%Y, %H:%M:%S")))
        
            # Testing
            print("\t\tValidation: {}".format(fold_index), end = " -- ")
            print("Start: {}".format(datetime.now().strftime("%m/%d/%Y, %H:%M:%S")), end="---")
            y_pred = model_svc.predict(x_test)
            print("End: {}".format(datetime.now().strftime("%m/%d/%Y, %H:%M:%S")))
        
            # Evaluation
            cm = confusion_matrix(y_test, y_pred)
            current_utils = utils(cm, y_test, y_pred)
            output_dict["fold_{}".format(fold_index)] = current_utils.get_value()
            
            fold_index += 1
        print("\n")
        return output_dict 
    
    def train(self, path):
        count = 0
        for x in self.param_grid["kernel"]:
            for i in self.param_grid["degree"]:
                for j in self.param_grid["gamma"]:
                    for k in self.param_grid["class_weight"]:
                        print("Traning Case: {}".format(count))
                        self.history["train_{}".format(count)] = {
                            "param" : {
                                "kernel" : x,
                                "degree" : i,
                                "gamma" : j,
                                "class_weight" : k,
                            },
                            "train_fold" : self.training(x, i, j, k, count)
                        }
                        count += 1
        with open(path.format(self.fold_count), 'wb') as f:
            pickle.dump(self.history, f)
        
        return self.history

# Training

In [11]:
training = Training(10, kmean_train_paths, kmean_test_paths)
approach_dir = os.getcwd() + "\\Experiment\\Approach"
svm_dir = approach_dir + "\\SVM"
save_result_path = svm_dir + '\\svm2-8_km64_surf_result_fold{0}_0.9.pkl'
training.train(path = save_result_path)

Traning Case: 0
	Fold: 0
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index0.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index0.csv
		Training : 0 -- Start: 12/05/2022, 14:07:15 --- End: 12/05/2022, 14:07:15
		Validation: 0 -- Start: 12/05/2022, 14:07:15---End: 12/05/2022, 14:07:15
	Fold: 1
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index1.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index1.csv
		Training : 1 -- Start: 12/05/2022, 14:07:15 --- End: 12/05/2022, 14:07:15
		Validation: 1 -- Start: 12/05/2022, 14:07:15---End: 12/05/2022, 14:07:15
	Fold: 2
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_

C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:15: RuntimeWarning: invalid value encountered in longlong_scalars
  self.precision = self.TP/(self.FN +  self.TP) # Precision Score - Positive Predictive Value
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:16: RuntimeWarning: invalid value encountered in longlong_scalars
  self.recall = self.TP / (self.TP + self.FN)
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:17: RuntimeWarning: invalid value encountered in longlong_scalars
  self.f1_score =  (2 * self.TP) / (2 * self.TP + self.FP + self.FN)
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:18: RuntimeWarning: invalid value encountered in longlong_scalars
  self.sensitivity = self.TP / (self.TP + self.FN) # True Positive Rate
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:21: RuntimeWarning: invalid value encountered in longlong_scalars
  self.false_negative_rate = self.FN / (self.FN + self.TP) # False Ne

	Fold: 3
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index3.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index3.csv
		Training : 3 -- Start: 12/05/2022, 14:07:16 --- End: 12/05/2022, 14:07:16
		Validation: 3 -- Start: 12/05/2022, 14:07:16---End: 12/05/2022, 14:07:16
	Fold: 4
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index4.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index4.csv
		Training : 4 -- Start: 12/05/2022, 14:07:16 --- End: 12/05/2022, 14:07:16
		Validation: 4 -- Start: 12/05/2022, 14:07:16---End: 12/05/2022, 14:07:16


C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:15: RuntimeWarning: invalid value encountered in longlong_scalars
  self.precision = self.TP/(self.FN +  self.TP) # Precision Score - Positive Predictive Value
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:16: RuntimeWarning: invalid value encountered in longlong_scalars
  self.recall = self.TP / (self.TP + self.FN)
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:17: RuntimeWarning: invalid value encountered in longlong_scalars
  self.f1_score =  (2 * self.TP) / (2 * self.TP + self.FP + self.FN)
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:18: RuntimeWarning: invalid value encountered in longlong_scalars
  self.sensitivity = self.TP / (self.TP + self.FN) # True Positive Rate
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:21: RuntimeWarning: invalid value encountered in longlong_scalars
  self.false_negative_rate = self.FN / (self.FN + self.TP) # False Ne

	Fold: 5
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index5.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index5.csv
		Training : 5 -- Start: 12/05/2022, 14:07:16 --- End: 12/05/2022, 14:07:16
		Validation: 5 -- Start: 12/05/2022, 14:07:16---End: 12/05/2022, 14:07:16
	Fold: 6
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index6.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index6.csv
		Training : 6 -- Start: 12/05/2022, 14:07:16 --- End: 12/05/2022, 14:07:16
		Validation: 6 -- Start: 12/05/2022, 14:07:16---End: 12/05/2022, 14:07:16


...

	Fold: 5
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index5.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index5.csv
		Training : 5 -- Start: 12/05/2022, 14:08:17 --- End: 12/05/2022, 14:08:17
		Validation: 5 -- Start: 12/05/2022, 14:08:17---End: 12/05/2022, 14:08:17
	Fold: 6
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index6.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index6.csv
		Training : 6 -- Start: 12/05/2022, 14:08:17 --- End: 12/05/2022, 14:08:17
		Validation: 6 -- Start: 12/05/2022, 14:08:17---End: 12/05/2022, 14:08:17
	Fold: 7
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index7.cs

C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:15: RuntimeWarning: invalid value encountered in longlong_scalars
  self.precision = self.TP/(self.FN +  self.TP) # Precision Score - Positive Predictive Value
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:16: RuntimeWarning: invalid value encountered in longlong_scalars
  self.recall = self.TP / (self.TP + self.FN)
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:17: RuntimeWarning: invalid value encountered in longlong_scalars
  self.f1_score =  (2 * self.TP) / (2 * self.TP + self.FP + self.FN)
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:18: RuntimeWarning: invalid value encountered in longlong_scalars
  self.sensitivity = self.TP / (self.TP + self.FN) # True Positive Rate
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:21: RuntimeWarning: invalid value encountered in longlong_scalars
  self.false_negative_rate = self.FN / (self.FN + self.TP) # False Ne

	Fold: 8
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index8.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index8.csv
		Training : 8 -- Start: 12/05/2022, 14:08:17 --- End: 12/05/2022, 14:08:17
		Validation: 8 -- Start: 12/05/2022, 14:08:17---End: 12/05/2022, 14:08:17
	Fold: 9
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index9.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index9.csv
		Training : 9 -- Start: 12/05/2022, 14:08:17 --- End: 12/05/2022, 14:08:17
		Validation: 9 -- Start: 12/05/2022, 14:08:17---End: 12/05/2022, 14:08:17




C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:15: RuntimeWarning: invalid value encountered in longlong_scalars
  self.precision = self.TP/(self.FN +  self.TP) # Precision Score - Positive Predictive Value
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:16: RuntimeWarning: invalid value encountered in longlong_scalars
  self.recall = self.TP / (self.TP + self.FN)
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:17: RuntimeWarning: invalid value encountered in longlong_scalars
  self.f1_score =  (2 * self.TP) / (2 * self.TP + self.FP + self.FN)
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:18: RuntimeWarning: invalid value encountered in longlong_scalars
  self.sensitivity = self.TP / (self.TP + self.FN) # True Positive Rate
C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:21: RuntimeWarning: invalid value encountered in longlong_scalars
  self.false_negative_rate = self.FN / (self.FN + self.TP) # False Ne

{'train_0': {'param': {'kernel': 'linear',
   'degree': 1,
   'gamma': 'scale',
   'class_weight': 'balanced'},
  'train_fold': {'fold_0': {'Confusion Matrix': {'TP': 3,
     'TN': 21,
     'FN': 2,
     'FP': 2,
     'precision': 0.6,
     'recall': 0.6,
     'f1_score': 0.6,
     'sensitivity': 0.6,
     'specificity': 0.9130434782608695,
     'negative_predictive_value': 0.9130434782608695,
     'false_negative_rate': 0.4,
     'false_positive_rate': 0.08695652173913043,
     'false_discovery_rate': 0.4,
     'false_omission_rate': 0.08695652173913043,
     'Positive_likelihood_ratio': 6.9,
     'Negative_likelihood_ratio': 0.43809523809523815,
     'prevalence_threshold': 0.27572628937504057,
     'threat_score': 0.12,
     'Prevalence': 0.17857142857142858,
     'Matthews_correlation_coefficient': 0.004461247637051039,
     'Fowlkes_Mallows_index': 1.0954451150103321,
     'informedness': 0.5130434782608695,
     'markedness': 0.5130434782608695,
     'Diagnostic_odds_ratio': 15.7

# Result Analyzing

In [12]:
file = open(save_result_path.format(10), 'rb')
result = pickle.load(file)
result

{'train_0': {'param': {'kernel': 'linear',
   'degree': 1,
   'gamma': 'scale',
   'class_weight': 'balanced'},
  'train_fold': {'fold_0': {'Confusion Matrix': {'TP': 3,
     'TN': 21,
     'FN': 2,
     'FP': 2,
     'precision': 0.6,
     'recall': 0.6,
     'f1_score': 0.6,
     'sensitivity': 0.6,
     'specificity': 0.9130434782608695,
     'negative_predictive_value': 0.9130434782608695,
     'false_negative_rate': 0.4,
     'false_positive_rate': 0.08695652173913043,
     'false_discovery_rate': 0.4,
     'false_omission_rate': 0.08695652173913043,
     'Positive_likelihood_ratio': 6.9,
     'Negative_likelihood_ratio': 0.43809523809523815,
     'prevalence_threshold': 0.27572628937504057,
     'threat_score': 0.12,
     'Prevalence': 0.17857142857142858,
     'Matthews_correlation_coefficient': 0.004461247637051039,
     'Fowlkes_Mallows_index': 1.0954451150103321,
     'informedness': 0.5130434782608695,
     'markedness': 0.5130434782608695,
     'Diagnostic_odds_ratio': 15.7

In [13]:
print("Number of Training: {}".format(len(list(result.keys()))))

Number of Training: 72


In [14]:
training_case_lst = list(result.keys())
print(training_case_lst[0])

train_0


In [15]:
train_sample = result[training_case_lst[0]]
print(train_sample['param'])
print("Number of Fold: {}".format(len(train_sample['train_fold'])))

{'kernel': 'linear', 'degree': 1, 'gamma': 'scale', 'class_weight': 'balanced'}
Number of Fold: 10


In [16]:
fold_sample = train_sample['train_fold']['fold_0']
print(fold_sample['Classification Report'])

{'0': {'precision': 0.6, 'recall': 0.375, 'f1-score': 0.4615384615384615, 'support': 8}, '1': {'precision': 0.8076923076923077, 'recall': 0.9130434782608695, 'f1-score': 0.8571428571428572, 'support': 23}, 'accuracy': 0.7741935483870968, 'macro avg': {'precision': 0.7038461538461538, 'recall': 0.6440217391304348, 'f1-score': 0.6593406593406593, 'support': 31}, 'weighted avg': {'precision': 0.7540942928039702, 'recall': 0.7741935483870968, 'f1-score': 0.7550514002126906, 'support': 31}}


In [17]:
result_analyze_dict = {
    'Train' : [],
    'MACC' : [],
    'MAP' : [],
    'MASens' : [],
    'MASpec' : [],
    'MAF1' : [],
    'AUC' : []
}

for result_key in result:
    result_analyze_dict['Train'].append(result_key)
    train_base = result[result_key]
    fold_base = train_base['train_fold']
    acc_lst, pre_lst, re_lst, spec_lst, f1_lst, auc_lst = [], [], [], [], [], []
    for fold_key in fold_base:
        current_fold = fold_base[fold_key]
        current_fold_cls = current_fold['Classification Report']
        acc_lst.append(current_fold_cls['accuracy'])
        pre_lst.append(current_fold_cls['macro avg']['precision'])
        re_lst.append(current_fold_cls['macro avg']['recall'])
        spec_lst.append(current_fold['Confusion Matrix']['specificity'])
        auc_lst.append(current_fold['ROC_AUC_SCORE']['Macro'])
        f1_lst.append(current_fold_cls['macro avg']['f1-score'])
    result_analyze_dict['MACC'].append(sum(acc_lst)/len(acc_lst))
    result_analyze_dict['MAP'].append(sum(pre_lst)/len(pre_lst))
    result_analyze_dict['MASens'].append(sum(re_lst)/len(re_lst))
    result_analyze_dict['MASpec'].append(sum(spec_lst)/len(spec_lst))
    result_analyze_dict['MAF1'].append(sum(f1_lst)/len(f1_lst))
    result_analyze_dict['AUC'].append(sum(auc_lst)/len(auc_lst))

result_df = pd.DataFrame(result_analyze_dict)
result_df.head()

Train      MACC       MAP    MASens    MASpec      MAF1       AUC
0  train_0  0.636559  0.349955  0.514402  0.891304  0.406447  0.514402
1  train_1  0.681720  0.340860  0.500000  1.000000  0.405185  0.500000
2  train_2  0.636559  0.349955  0.514402  0.891304  0.406447  0.514402
3  train_3  0.681720  0.340860  0.500000  1.000000  0.405185  0.500000
4  train_4  0.636559  0.349955  0.514402  0.891304  0.406447  0.514402

In [18]:
result_max = result_df.max()
result_max

Train      train_9
MACC      0.870968
MAP       0.863651
MASens    0.874366
MASpec         1.0
MAF1      0.856024
AUC       0.874366
dtype: object

In [19]:
id_result_max = result_df.iloc[:, 1:].idxmax()
id_result_max

MACC      24
MAP       25
MASens    24
MASpec     1
MAF1      24
AUC       24
dtype: int64

In [20]:
id_max = 'train_{}'.format(id_result_max.mode()[0])
print(id_max)

train_24


In [21]:
result_df.loc[result_df['Train'] == id_max]

Train      MACC      MAP    MASens    MASpec      MAF1       AUC
24  train_24  0.870968  0.85859  0.874366  0.865399  0.856024  0.874366

In [22]:
train_max = result[id_max]
train_max['param']

{'kernel': 'rbf', 'degree': 1, 'gamma': 'scale', 'class_weight': 'balanced'}

In [23]:
train_max_fold = train_max['train_fold']
train_max_analyze = {
    'Fold' : [],
    'ACC' : [],
    'AP' : [],
    'ASens' : [],
    'ASpec' : [],
    'AF1' : [],
    'AUC' : []
}

for fold_key in train_max_fold:
    train_max_analyze['Fold'].append(fold_key)
    current_fold = train_max_fold[fold_key]
    current_fold_cls = current_fold['Classification Report']
    train_max_analyze['ACC'].append(current_fold_cls['accuracy'])
    train_max_analyze['AP'].append(current_fold_cls['macro avg']['precision'])
    train_max_analyze['ASens'].append(current_fold_cls['macro avg']['recall'])
    train_max_analyze['ASpec'].append(current_fold['Confusion Matrix']['specificity'])
    train_max_analyze['AF1'].append(current_fold_cls['macro avg']['f1-score'])
    train_max_analyze['AUC'].append(current_fold['ROC_AUC_SCORE']['Macro'])

train_max_analyze_df = pd.DataFrame(train_max_analyze)
train_max_analyze_df

Fold       ACC        AP     ASens     ASpec       AF1       AUC
0  fold_0  0.838710  0.787879  0.809783  0.869565  0.797386  0.809783
1  fold_1  0.888889  0.875000  0.875000  0.916667  0.875000  0.875000
2  fold_2  0.888889  0.928571  0.833333  1.000000  0.861538  0.833333
3  fold_3  0.888889  0.875000  0.875000  0.916667  0.875000  0.875000
4  fold_4  0.805556  0.785714  0.812500  0.791667  0.792593  0.812500
5  fold_5  0.861111  0.852941  0.895833  0.791667  0.855654  0.895833
6  fold_6  0.972222  0.961538  0.979167  0.958333  0.969362  0.979167
7  fold_7  0.888889  0.870130  0.895833  0.875000  0.879599  0.895833
8  fold_8  0.805556  0.815789  0.854167  0.708333  0.801731  0.854167
9  fold_9  0.870968  0.833333  0.913043  0.826087  0.852381  0.913043

# N_times_K_folds

In [24]:
# Setup

train_max_param = train_max['param']
n_times = 100

nt_kf_output_dict = {
    'Train' : [], # <index>_<fold>
    'ACC' : [],
    'AP' : [],
    'ASens' : [],
    'ASpec' : [],
    'AF1' : [],
    'AUC' : []
}

for n in range(n_times):
    print("Training {}".format(n))
    fold_index = 0
    for train_index, test_index in zip(kmean_train_paths, kmean_test_paths):
        train_df = pd.read_csv(train_index)
        test_df = pd.read_csv(test_index)      
    
        print("\tFold: {}".format(fold_index))
        print("\tTRAIN:", train_index, "\n\tTEST:", test_index)

        # folding data
        x_train, y_train = train_df.iloc[:, 2:-1], train_df.iloc[:, -1]
        x_test, y_test = test_df.iloc[:, 2:-1], test_df.iloc[:, -1]
        
        # Training
        print("\t\tTraining : {}".format(fold_index), end = " -- ")
        print("Start: {}".format(datetime.now().strftime("%m/%d/%Y, %H:%M:%S")), end=" --- ")
        model_svc = SVC(kernel = train_max_param['kernel'], 
                        degree = train_max_param['degree'], 
                        gamma = train_max_param['gamma'], 
                        class_weight = train_max_param['class_weight']
                       )
        model_svc.fit(x_train, y_train)
        print("End: {}".format(datetime.now().strftime("%m/%d/%Y, %H:%M:%S")))

        # Testing
        print("\t\tValidation: {}".format(fold_index), end = " -- ")
        print("Start: {}".format(datetime.now().strftime("%m/%d/%Y, %H:%M:%S")), end="---")
        y_pred = model_svc.predict(x_test)
        print("End: {}".format(datetime.now().strftime("%m/%d/%Y, %H:%M:%S")))
        
        # Evaluation
        cm = confusion_matrix(y_test, y_pred)
        base_result = utils(cm, y_test, y_pred).get_value()
        
        # Result Storing
        nt_kf_output_dict['Train'].append('{0}_{1}'.format(n, fold_index))
        cls = base_result['Classification Report']
        nt_kf_output_dict['ACC'].append(cls['accuracy'])
        nt_kf_output_dict['AP'].append(cls['macro avg']['precision'])
        nt_kf_output_dict['ASens'].append(cls['macro avg']['recall'])
        nt_kf_output_dict['ASpec'].append(base_result['Confusion Matrix']['specificity'])
        nt_kf_output_dict['AF1'].append(cls['macro avg']['f1-score'])
        nt_kf_output_dict['AUC'].append(base_result['ROC_AUC_SCORE']['Macro'])
        
        # Fold index increment
        fold_index += 1

Training 0
	Fold: 0
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index0.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index0.csv
		Training : 0 -- Start: 12/05/2022, 14:08:19 --- End: 12/05/2022, 14:08:19
		Validation: 0 -- Start: 12/05/2022, 14:08:19---End: 12/05/2022, 14:08:19
	Fold: 1
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index1.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index1.csv
		Training : 1 -- Start: 12/05/2022, 14:08:19 --- End: 12/05/2022, 14:08:19
		Validation: 1 -- Start: 12/05/2022, 14:08:19---End: 12/05/2022, 14:08:19
	Fold: 2
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_c

C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:25: RuntimeWarning: divide by zero encountered in double_scalars
  self.positive_likelihood_ratio = self.sensitivity / self.false_positive_rate # Positive Likelihood Ratio


	Fold: 3
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index3.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index3.csv
		Training : 3 -- Start: 12/05/2022, 14:08:20 --- End: 12/05/2022, 14:08:20
		Validation: 3 -- Start: 12/05/2022, 14:08:20---End: 12/05/2022, 14:08:20
	Fold: 4
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index4.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index4.csv
		Training : 4 -- Start: 12/05/2022, 14:08:20 --- End: 12/05/2022, 14:08:20
		Validation: 4 -- Start: 12/05/2022, 14:08:20---End: 12/05/2022, 14:08:20
	Fold: 5
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index5.cs

C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:25: RuntimeWarning: divide by zero encountered in double_scalars
  self.positive_likelihood_ratio = self.sensitivity / self.false_positive_rate # Positive Likelihood Ratio


	Fold: 3
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index3.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index3.csv
		Training : 3 -- Start: 12/05/2022, 14:08:21 --- End: 12/05/2022, 14:08:21
		Validation: 3 -- Start: 12/05/2022, 14:08:21---End: 12/05/2022, 14:08:21
	Fold: 4
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index4.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index4.csv
		Training : 4 -- Start: 12/05/2022, 14:08:21 --- End: 12/05/2022, 14:08:21
		Validation: 4 -- Start: 12/05/2022, 14:08:21---End: 12/05/2022, 14:08:21
	Fold: 5
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index5.cs

...

	Fold: 5
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index5.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index5.csv
		Training : 5 -- Start: 12/05/2022, 14:09:44 --- End: 12/05/2022, 14:09:44
		Validation: 5 -- Start: 12/05/2022, 14:09:44---End: 12/05/2022, 14:09:44
	Fold: 6
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index6.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index6.csv
		Training : 6 -- Start: 12/05/2022, 14:09:44 --- End: 12/05/2022, 14:09:44
		Validation: 6 -- Start: 12/05/2022, 14:09:44---End: 12/05/2022, 14:09:44
	Fold: 7
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index7.cs

C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:25: RuntimeWarning: divide by zero encountered in double_scalars
  self.positive_likelihood_ratio = self.sensitivity / self.false_positive_rate # Positive Likelihood Ratio


	Fold: 4
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index4.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index4.csv
		Training : 4 -- Start: 12/05/2022, 14:09:44 --- End: 12/05/2022, 14:09:44
		Validation: 4 -- Start: 12/05/2022, 14:09:44---End: 12/05/2022, 14:09:44
	Fold: 5
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index5.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index5.csv
		Training : 5 -- Start: 12/05/2022, 14:09:44 --- End: 12/05/2022, 14:09:44
		Validation: 5 -- Start: 12/05/2022, 14:09:44---End: 12/05/2022, 14:09:44
	Fold: 6
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index6.cs

C:\Users\KohiDo\AppData\Local\Temp\ipykernel_13400\425510141.py:25: RuntimeWarning: divide by zero encountered in double_scalars
  self.positive_likelihood_ratio = self.sensitivity / self.false_positive_rate # Positive Likelihood Ratio


	Fold: 3
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index3.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index3.csv
		Training : 3 -- Start: 12/05/2022, 14:09:45 --- End: 12/05/2022, 14:09:45
		Validation: 3 -- Start: 12/05/2022, 14:09:45---End: 12/05/2022, 14:09:45
	Fold: 4
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index4.csv 
	TEST: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_test_50_4_3_True_Falsehisto_512_cv_index4.csv
		Training : 4 -- Start: 12/05/2022, 14:09:45 --- End: 12/05/2022, 14:09:45
		Validation: 4 -- Start: 12/05/2022, 14:09:45---End: 12/05/2022, 14:09:45
	Fold: 5
	TRAIN: D:\Github\Stomach-Status-Classification\Data set\kmean_dataset2-8\10cv_512\surf_train_50_4_3_True_Falsehisto_512_cv_index5.cs

In [25]:
nt_kf_output_df = pd.DataFrame(nt_kf_output_dict)
nt_kf_output_df.head(10)

Train       ACC        AP     ASens     ASpec       AF1       AUC
0   0_0  0.838710  0.787879  0.809783  0.869565  0.797386  0.809783
1   0_1  0.888889  0.875000  0.875000  0.916667  0.875000  0.875000
2   0_2  0.888889  0.928571  0.833333  1.000000  0.861538  0.833333
3   0_3  0.888889  0.875000  0.875000  0.916667  0.875000  0.875000
4   0_4  0.805556  0.785714  0.812500  0.791667  0.792593  0.812500
5   0_5  0.861111  0.852941  0.895833  0.791667  0.855654  0.895833
6   0_6  0.972222  0.961538  0.979167  0.958333  0.969362  0.979167
7   0_7  0.888889  0.870130  0.895833  0.875000  0.879599  0.895833
8   0_8  0.805556  0.815789  0.854167  0.708333  0.801731  0.854167
9   0_9  0.870968  0.833333  0.913043  0.826087  0.852381  0.913043

In [26]:
nt_kf_output_df.mean()

Train         inf
ACC      0.870968
AP       0.858590
ASens    0.874366
ASpec    0.865399
AF1      0.856024
AUC      0.874366
dtype: float64

In [27]:
nt_kf_output_df.std(numeric_only=True)

ACC      0.046102
AP       0.053860
ASens    0.048493
ASpec    0.083233
AF1      0.049598
AUC      0.048493
dtype: float64

In [28]:
acc_values = nt_kf_output_df['ACC'].values.tolist()
ap_values = nt_kf_output_df['AP'].values.tolist()
asens_values = nt_kf_output_df['ASens'].values.tolist()
aspec_values = nt_kf_output_df['ASpec'].values.tolist()
af1_values = nt_kf_output_df['AF1'].values.tolist()
auc_values = nt_kf_output_df['AUC'].values.tolist()
print(len(acc_values), len(ap_values), len(asens_values), len(aspec_values), len(af1_values), len(auc_values))

1000 1000 1000 1000 1000 1000


In [29]:
import scipy.stats as st

def CI(data, confidence_level, dis_type = 't'):
    if dis_type == 't':
        return st.t.interval(confidence=confidence_level, df=len(data)-1, 
                             loc=np.mean(data), scale=st.sem(data))
    elif dis_type == 'g':
        return st.norm.interval(confidence=confidence_level, loc=np.mean(data), scale=st.sem(data))

def CI_calculator(confidence_level, dis_type = 't'):
    for x in nt_kf_output_df.columns[1:]:
        base = nt_kf_output_df[x].values.tolist()
        print("CI of {}".format(x), CI(base, confidence_level, dis_type))

In [30]:
cl = 0.95

CI_calculator(confidence_level = cl, dis_type = 't')

CI of ACC (0.8681069174419972, 0.8738285664289706)
CI of AP (0.855247405833859, 0.8619319576303344)
CI of ASens (0.8713567537365172, 0.8773751303214539)
CI of ASpec (0.8602335369482745, 0.8705635645010008)
CI of AF1 (0.8529464648051085, 0.8591020313672165)
CI of AUC (0.8713567537365172, 0.8773751303214539)


In [31]:
cl = 0.95

CI_calculator(confidence_level = cl, dis_type = 'g')

CI of ACC (0.8681103834765308, 0.873825100394437)
CI of AP (0.8552514551712828, 0.8619279082929107)
CI of ASens (0.8713603995213473, 0.8773714845366238)
CI of ASpec (0.8602397946254429, 0.8705573068238325)
CI of AF1 (0.8529501936962598, 0.8590983024760652)
CI of AUC (0.8713603995213473, 0.8773714845366238)


In [32]:
cl = 0.99

CI_calculator(confidence_level = cl, dis_type = 'g')

CI of ACC (0.8672125363769277, 0.87472294749404)
CI of AP (0.8542025083630679, 0.8629768551011255)
CI of ASens (0.870415989618991, 0.8783158944389801)
CI of ASpec (0.8586187959766003, 0.872178305472675)
CI of AF1 (0.8519842558002467, 0.8600642403720783)
CI of AUC (0.870415989618991, 0.8783158944389801)
